# 東森新聞雲爬蟲練習
## 練習從東森新聞雲網站中，爬取新聞摘要及詳細內容。
## 學習利用Selenium模擬人為操作，更新動態網頁後爬取新聞內容。

In [1]:
import requests
import time
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.keys import Keys

### 以財經新聞為例，先連結到財經新聞網頁，複製其URL。

In [2]:
ETtoday_url = "https://www.ettoday.net/news/focus/%E8%B2%A1%E7%B6%93/"  #財經新聞

### 用Selenium打開一個瀏覽器，連結到網站。然後模擬下拉網頁的動作，讓網頁完成更新，再處理後續動作。

In [3]:
browser = webdriver.Chrome()
browser.get(ETtoday_url)  # 打開瀏覽器並連到東森新聞雲網頁

SCROLL_PAUSE_TIME = 1
'''
Your code here
提示：可參考以下的Stack Overflow: 
https://stackoverflow.com/questions/48850974/selenium-scroll-to-end-of-page-indynamically-loading-webpage/48851166

'''

#
# 以下是用Selenium模擬下拉網頁動作，讓網頁更新
#
# last_height = browser.execute_script("window.scrollTo(0, document.body.scrollHeight);")
# print("目前高度 ",last_height)
# # 以下是用Selenium模擬下拉網頁動作，讓網頁更新
# # scrollWidth和scrollHeight屬性返回元素的整個高度和寬度，包括不可見的高度和寬度（由於溢出）
count1=0
while True:
    last_height = browser.execute_script("return document.body.scrollHeight;")
#     last_height = browser.execute_script("window.scrollTo(0, document.body.scrollHeight);")#有問題
    print("目前高度 ",last_height)
    # # 以下是用Selenium模擬下拉網頁動作，讓網頁更新
    # # scrollWidth和scrollHeight屬性返回元素的整個高度和寬度，包括不可見的高度和寬度（由於溢出）

    #print('網頁更新中...')
    # Scroll down to the bottom.# 抓到整個瀏覽器高度，然後滑下去
    browser.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    # Wait to load the page.
    #time.sleep(2)   # 等2秒
    time.sleep(SCROLL_PAUSE_TIME)
    # Calculate new scroll height and compare with last scroll height.
    # 計算新高度，與舊的高度比一比，若一樣代表到底了
    current_height = browser.execute_script("return document.body.scrollHeight;")
    if current_height == last_height:
        print("目前高度 ",last_height," 轉動後 高度 ",current_height,'到達頁面底端')
        break #break語句用來終止循環語句
    else:
        count1=count1+1
        print(count1," 轉動後 高度 ",current_height,' 網頁更新中...')
# last_height = current_height
# continu #break跳出整個循環

目前高度  6843
1  轉動後 高度  9163  網頁更新中...
目前高度  9163
2  轉動後 高度  11521  網頁更新中...
目前高度  11521
3  轉動後 高度  13773  網頁更新中...
目前高度  13773
4  轉動後 高度  16105  網頁更新中...
目前高度  16105
5  轉動後 高度  18500  網頁更新中...
目前高度  18500
6  轉動後 高度  20884  網頁更新中...
目前高度  20884
7  轉動後 高度  23257  網頁更新中...
目前高度  23257
8  轉動後 高度  24661  網頁更新中...
目前高度  24661
9  轉動後 高度  24711  網頁更新中...
目前高度  24711
目前高度  24711  轉動後 高度  24711 到達頁面底端


### 到這裡網頁已經更新完畢，所有的新聞都已經出現在網頁上。接下來做爬取收集新聞的動作。

In [4]:
#
# 這裡先建立一個函數，其功能是連到外部連結，並爬取新聞內容。
#
def getNewsDetailContent(link_url):
#     headers = {
#     'Connection': 'close',
#     }

#     resp = requests.get(link_url, headers=headers)
    resp = requests.get(link_url)
    resp.encoding = 'utf-8'
    print(resp.text)

    #https://www.ettoday.net/news/20200118/1628408.htm

    soup = BeautifulSoup(resp.text, 'lxml')
    news_content = soup.find("div", attrs={'class':'story'}).find_all("p")
#     #<div class="story" itemprop="articleBody"
#         <!-- 投票 文章前 開始 -->
#         <!-- 投票 文章前 結束 -->
#         <!-- 文章內容 開始 -->
#         <p class="no_margin"><img src="//cdn2.ettoday.net/images/4657/d4657843.jpg" alt="▲▼「2000萬超級紅包」百萬得主現身，分享幸運中獎過程。（圖／記者紀佳妘攝）" width="600" height="450" title="▲▼「2000萬超級紅包」百萬得主現身，分享幸運中獎過程。（圖／記者紀佳妘攝）"></p>
#         <p><strong class="figcaption">▲「2000萬超級紅包」百萬得主現身，分享幸運中獎過程。（圖／記者紀佳妘攝）</strong></p>
#         <p>記者紀佳妘／台北報導</p>
    for p in news_content:
        """
        .string屬性說明：
        (1) 若當前tag節點底下沒有其他tag子節點，會直接抓取內容(返回"NavigableString")
        (2) 若當前tag節點底下只有唯一的一個tag子節點，也會直接抓取tag子節點的內容(返回"NavigableString")
        (3) 但若當前tag節點底下還有很多個tag子節點，.string就無法判斷，(返回"None")
        """
        if ((p.string) is not None):
            print(p.string)

### 解析HTML並萃取新聞摘要，若有外部的連結，再連到外部連結並把詳細新聞內容抓取下來。

In [ ]:
# 爬取網頁內容，解析後萃取新聞摘要
html = browser.page_source
soup = BeautifulSoup(html, "lxml")
#新的庫不支持lxml,把函数参数中所有的"lxml"改成"html.parser",
#用python3.5自带的网页解析器也可以达到很理想的效果,只是html.parser的解析效果没有lxml好，快。
# ,windows系统 pip install wheel 在 import lxml
# pip install lxml

all_news = soup.find("div", attrs={'class':'block block_1 infinite_scroll'})
#<div class="block block_1 infinite_scroll">

news_block = all_news.find_all('div', attrs={'class':'piece clearfix'})
# <!--part_pictxt_3 圖文列表 開始-->
#   <div class="part_pictxt_3 lazyload">
#       <div class="piece clearfix">
#           <a href="/news/20200118/1628408.htm" class="pic" title="新店幸運得主現身！　七年級生靠女友「幸運密碼」刮中100萬"><img src="//cdn2.ettoday.net/images/4657/c4657843.jpg" data-original="//cdn2.ettoday.net/images/4657/c4657843.jpg" alt="新店幸運得主現身！　七年級生靠女友「幸運密碼」刮中100萬" style="display: block;"></a>
#           <h3><a href="/news/20200118/1628408.htm" title="新店幸運得主現身！　七年級生靠女友「幸運密碼」刮中100萬">新店幸運得主現身！　七年級生靠女友「幸運密碼」刮中100萬</a></h3>
#           <p class="summary">台彩近期推出「2000萬超級紅包」，今（18）日三獎百萬得主現身新北市新店區的吉優彩券行，這名住在新店的七年級生用「幸運密碼」，當天刮了5張都沒中，直到第6張以他女友的出生年月挑選刮刮樂，幸運中了百萬..</p>
#           <span class="date">8小時前</span>
#       </div>

for i, news_item in enumerate(news_block):
    print("----------------------------------------------------------------------")
    news_body = news_item.find('h3')
    print("\n[%d] %s\n" % (i, news_body.a.string))

    # 
    # 連到外部連結，擷取詳細新聞內容
    #
    externalLink = "https://www.ettoday.net" + news_body.a["href"]
    getNewsDetailContent(externalLink)

----------------------------------------------------------------------

[0] 快訊／初七大樂透開獎！頭獎2億中了開啟第二人生　147組大紅包等你拿

<!doctype html>
<html lang="zh-Hant" prefix="og:http://ogp.me/ns#" xmlns:wb="http://open.weibo.com/wb" itemscope itemtype="http://schema.org/NewsArticle">
<head>
<meta charset="utf-8">
<!-- ★★★以下非共用★★★ 開始 -->
<link rel="amphtml" href="https://www.ettoday.net/amp/amp_news.php?news_id=1635441">
<title>快訊／初七大樂透開獎！頭獎2億中了開啟第二人生　147組大紅包等你拿 | ETtoday財經 | ETtoday新聞雲</title>

<link rel="canonical" itemprop="mainEntityOfPage" href="https://www.ettoday.net/news/20200131/1635441.htm"/>

<!-- 網頁社群分享meta 開始 -->
<meta property="og:url" itemprop="url" content="https://www.ettoday.net/news/20200131/1635441.htm"/>
<meta property="og:title" itemprop="name" content="快訊／初七大樂透開獎！頭獎2億中了開啟第二人生　147組大紅包等你拿 | ETtoday新聞雲"/>
<meta property="og:image" itemprop="image" content="https://cdn2.ettoday.net/images/4150/d4150340.jpg"/>
<meta property="og:image:width" content="1200"/>
<meta property="og:image:hei